In [ ]:
from pyscope.observatory import Observatory
from astropy import coordinates as coord
import logging

# Set up logging
logging.basicConfig(level=logging.DEBUG)

In [ ]:
rlmt = Observatory(config_path="./rlmt.cfg")
rlmt.connect_all()

In [ ]:
print(rlmt.recenter.__doc__)

In [30]:
src = coord.SkyCoord.from_name("M64")
print(f"RA: {src.ra.hms},\nDec: {src.dec.dms}")
print(src)
# Print alt az of source
src_altaz = rlmt.get_object_altaz(src)
print(f"Elevation: {src_altaz.alt.deg:.2f}, Azimuth: {src_altaz.az.deg:.2f}")
print(f"Elevation dms: {src_altaz.alt.dms}, \nAzimuth dms: {src_altaz.az.dms}")
if src_altaz.alt.deg < 30:
    raise Exception("Source is too low to observe.")
 
tete_coords = src.transform_to(coord.TETE(obstime = rlmt.observatory_time, location=rlmt.observatory_location))
print(tete_coords)
print(f"RA: {tete_coords.ra.hms},\nDec: {tete_coords.dec.dms}")

RA: hms_tuple(h=12.0, m=56.0, s=43.696008000012796),
Dec: dms_tuple(d=21.0, m=40.0, s=57.569879999999785)
<SkyCoord (ICRS): (ra, dec) in deg
    (194.1820667, 21.6826583)>
Elevation: 47.35, Azimuth: 91.87
Elevation dms: dms_tuple(d=47.0, m=20.0, s=57.97982308112353), 
Azimuth dms: dms_tuple(d=91.0, m=52.0, s=4.038177513159553)
<SkyCoord (TETE: obstime=2024-04-15 03:38:16.677161, location=(-1912250.53754772, -5087010.80082703, 3329502.27407335) m): (ra, dec, distance) in (deg, deg, )
    (194.4853231, 21.55006715, 1.)>
RA: hms_tuple(h=12.0, m=57.0, s=56.47754517831942),
Dec: dms_tuple(d=21.0, m=33.0, s=0.24173380448331727)


In [31]:
if src_altaz.alt.deg < 30:
    raise Exception("Source is too low to observe.")
rlmt.recenter(src, 
    target_x_pixel=1024, # TODO: make default center of sensor in each axis
    target_y_pixel=1024,
    exposure=3, 
    save_images=True,
    save_path="./recenter_images/",
    readout=2,
)

INFO:pyscope.observatory.observatory:Attempt 1 of 5
INFO:pyscope.observatory.observatory:Slewing to RA hms_tuple(h=12.0, m=56.0, s=43.69600800001919) and Dec dms_tuple(d=21.0, m=40.0, s=57.569879999999785)
INFO:pyscope.observatory.observatory:Turning on sidereal tracking...
INFO:pyscope.observatory.observatory:Sidereal tracking is on.
INFO:pyscope.observatory.observatory:Attempting to slew to coordinates...
INFO:pyscope.observatory.observatory:Slewing to RA 12.96569 and Dec 21.55007
INFO:pyscope.observatory.observatory:Settling for 0.00 seconds...
INFO:pyscope.observatory.observatory:Settling for 0.00 seconds
INFO:pyscope.observatory.observatory:Taking 3.00 second exposure
INFO:pyscope.observatory.observatory:Exposure complete
INFO:pyscope.observatory.observatory:Using Maxim to save image
INFO:pyscope.observatory.observatory:Overwrite allowed for header keys ['AIRMASS', 'OBJECT', 'TELESCOP', 'INSTRUME', 'OBSERVER']
INFO:pyscope.observatory.observatory:Getting header from MaxIm image
IN

True

# Recenter troubleshooting

In [ ]:
# Load image recenter_images\M51-0001_g.fts
import astropy.io.fits as fits
import astropy.wcs
import matplotlib.pyplot as plt
import numpy as np

src = coord.SkyCoord.from_name("M51")
print("Source: M51\n=============================")
print(f"RA: {src.ra.hms},\nDec: {src.dec.dms}")
print(src)
# Print alt az of source
src_altaz = rlmt.get_object_altaz(src)
print(f"Elevation: {src_altaz.alt.deg:.2f}, Azimuth: {src_altaz.az.deg:.2f}")
print(f"Elevation dms: {src_altaz.alt.dms}, \nAzimuth dms: {src_altaz.az.dms}")

hdr = fits.getheader("./recenter_images/M51-0001_g.fts")

wcs = astropy.wcs.WCS(hdr)
print("\nWCS \n=============================")
# Print center value in hms, dms
center = wcs.all_pix2world(1024, 1024, 1)
print(f"Center: {center}")
center = coord.SkyCoord(center[0], center[1], unit="deg")
print(f"Center: {center}")
print(f"Center: {center.ra.hms}, \n{center.dec.dms}")

center_coord = wcs.pixel_to_world(1024, 1024)
print(f"Center: {center_coord}")
print(f"Center: {center_coord.ra.hms}, \n{center_coord.dec.dms}")

print("Slew coordinates")
slew_coords = rlmt.get_object_slew(src)
print(slew_coords)
print(f"RA: {slew_coords.ra.hms},\nDec: {slew_coords.dec.dms}")

print("TETE coordinates")
tete_coords = src.transform_to(coord.TETE(obstime = rlmt.observatory_time, location=rlmt.observatory_location))
print(tete_coords)

print("icrs coordinates")
icrs_coords = src.transform_to(coord.ICRS)
print(icrs_coords)

In [ ]:
rlmt.observatory_time